In [98]:

from sklearn.base import TransformerMixin, BaseEstimator

from collections import Counter , defaultdict

import pandas as pd

pd.set_option('display.max_columns', None)


from pandas import Series as s , DataFrame as df
import numpy as np

import seaborn as sns
# import matplotlib.pyplot as plt

# To ignore warnings
import warnings
warnings.filterwarnings("ignore")

from matplotlib import pyplot as plt, rcParams as rc


%matplotlib inline
rc["figure.figsize"] = 10,6

import datetime
import datetime as dt

from sklearn.model_selection  import StratifiedKFold
from sklearn.decomposition import PCA

from iteration_utilities import duplicates, unique_everseen

import sys
from itertools import groupby
from operator import itemgetter
from timeit import timeit


## RandomOverSampler to handle imbalanced data
from imblearn.over_sampling import RandomOverSampler # over sampling method 2

In [99]:

#Algorithm
from sklearn.linear_model import LogisticRegression
from sklearn.svm import SVC
from sklearn.tree import DecisionTreeClassifier
from sklearn.ensemble import RandomForestClassifier
from xgboost import XGBClassifier

from sklearn.naive_bayes import MultinomialNB

from lightgbm import LGBMClassifier
# from catboost import CatBoostClassifier

#preprocessing
from sklearn.preprocessing import LabelEncoder

from sklearn.preprocessing import StandardScaler, normalize



from sklearn.model_selection import train_test_split

import lightgbm as lgb


#Metrics
from sklearn.metrics import accuracy_score, roc_auc_score, roc_curve, recall_score, precision_score
from sklearn.metrics import confusion_matrix, classification_report, f1_score, precision_recall_fscore_support

from sklearn.pipeline import Pipeline

# GridSearchCV to find optimal min_samples_leaf
from sklearn.model_selection import KFold
from sklearn.model_selection import GridSearchCV

In [168]:
df = pd.read_csv("train_Wc8LBpr.csv")

df_test = pd.read_csv("test_VsU9xXK.csv")
submission = pd.read_csv("sample_submission_NoPBkjr.csv")

df10 = df.copy()
df.shape, df_test.shape, submission.shape

((131662, 14), (87395, 13), (87395, 2))

In [101]:
def get_percentage_miss_value(dataset):
    higher_miss_value_column = []
    miss_threshold_value = 50
    
    for i in dataset.columns:
        if dataset[i].isna().sum() > 1: 
            perectange_val = (dataset[i].isna().sum() / len(dataset)) * 100
            print("Column-> " , i, ", total no of missing value : ",dataset[i].isna().sum() , " & :         ", round(perectange_val,2) ," %")
                
            if(perectange_val > miss_threshold_value):
                higher_miss_value_column.append(i)
            
    print("\n\n\n")
    
    if higher_miss_value_column:
        print("Higher Missing values in Columns for Delete : ", higher_miss_value_column)
    else:
        print("There are no Higher Column Missing values in Dataset")

In [102]:
# get_percentage_miss_value(df)

In [103]:
# get_percentage_miss_value(df_test)

In [104]:
 df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 131662 entries, 0 to 131661
Data columns (total 14 columns):
Trip_ID                        131662 non-null object
Trip_Distance                  131662 non-null float64
Type_of_Cab                    111452 non-null object
Customer_Since_Months          125742 non-null float64
Life_Style_Index               111469 non-null float64
Confidence_Life_Style_Index    111469 non-null object
Destination_Type               131662 non-null object
Customer_Rating                131662 non-null float64
Cancellation_Last_1Month       131662 non-null int64
Var1                           60632 non-null float64
Var2                           131662 non-null int64
Var3                           131662 non-null int64
Gender                         131662 non-null object
Surge_Pricing_Type             131662 non-null int64
dtypes: float64(5), int64(4), object(5)
memory usage: 14.1+ MB


In [105]:
def check_cloumn_details_type_categorical(dataset):
    for i in dataset.columns:
        if(dataset[i].dtype == "object"):
            print("Columns name :  ",i  )
            
            print(dict(Counter(dataset[i])))
            
            print("*"*100)
            print("\n")

In [106]:
# check_cloumn_details_type_categorical(df)

In [107]:
93900 / len(df)

0.7131898345764154

In [108]:
df.head()

Trip_ID  Trip_Distance Type_of_Cab  Customer_Since_Months  \
0  T0005689460           6.77           B                    1.0   
1  T0005689461          29.47           B                   10.0   
2  T0005689464          41.58         NaN                   10.0   
3  T0005689465          61.56           C                   10.0   
4  T0005689467          54.95           C                   10.0   

   Life_Style_Index Confidence_Life_Style_Index Destination_Type  \
0           2.42769                           A                A   
1           2.78245                           B                A   
2               NaN                         NaN                E   
3               NaN                         NaN                A   
4           3.03453                           B                A   

   Customer_Rating  Cancellation_Last_1Month  Var1  Var2  Var3  Gender  \
0          3.90500                         0  40.0    46    60  Female   
1          3.45000                         0  38.0    56    78    Male   
2          3.50125                         2   NaN    56    77    Male   
3          3.45375                         0   NaN    52    74    Male   
4          3.40250                         4  51.0    49   102    Male   

   Surge_Pricing_Type  
0                   2  
1                   2  
2                   2  
3                   3  
4                   2

In [109]:
# check_cloumn_details_type_categorical(df_test)

In [110]:
def check_cloumn_details_type_numberical(dataset):
    for i in dataset.columns:
        if (dataset[i].dtype == "int"):
            print("Columns name :  ",i  )
            
            print(dict(Counter(dataset[i])))
            print("*"*100)
            print("\n")
            
            
def check_cloumn_details_type_float(dataset):
    for i in dataset.columns:
        if (dataset[i].dtype == "float"):
            print("Columns name :  ",i  )
            
            print(dict(Counter(dataset[i])))
            print("*"*100)
            print("\n")
            

In [111]:
#check_cloumn_details_type_numberical(df)

In [112]:
# check_cloumn_details_type_float(df)

In [113]:
# Visulazing the distibution of the data for every feature
def visualize_hist(dataset):
    dataset.hist(edgecolor='black', linewidth=1.2, figsize=(20, 20));
    plt.show()

In [114]:
# visualize_hist(df)

In [115]:
def visualize_histogram(dataset):
    # plot histogram
    plt.figure(figsize=(25, 9))  # figure size in ratio 16:9
    features = dataset.columns  # list of columns name
    for i, j in enumerate(features):
        plt.subplot(3, 3, i + 1)  # create subplot for histogram
        plt.title("Histogram of {}".format(j), fontsize=15)  # title of histogram

        bins = len(dataset[j].unique())  # bins for histogram
        plt.hist(dataset[j], bins=bins, rwidth=0.8, edgecolor="y", linewidth=2, )  # plot histogram

    plt.subplots_adjust(hspace=0.5)  # space between horixontal axes (subplots)

In [116]:
# visualize_histogram(df)

In [117]:

    
def corr_metrix(dataset):
    corr = dataset.corr()
    # Generate a mask for the upper triangle
    mask = np.zeros_like(corr, dtype=np.bool)
    mask[np.triu_indices_from(mask)] = True

    # Set up the matplotlib figure
    f, ax = plt.subplots(figsize=(11, 9))

    # Generate a custom diverging colormap
    cmap = sns.diverging_palette(220, 10, as_cmap='RdYlGn')

    # Draw the heatmap with the mask and correct aspect ratio
    sns.heatmap(corr, mask=mask, cmap=cmap, vmax=1, center=0,
            square=True, linewidths=.5, cbar_kws={"shrink": .5});
    ax.tick_params(labelsize=20)

def corr_2_more_visualize(dataset):
    corr = dataset.corr()
    
    f, ax = plt.subplots(figsize=(20, 9))
    sns.heatmap(corr.apply(lambda x : np.round(x,2)), 
            xticklabels=corr.columns.values,
            yticklabels=corr.columns.values,annot=True,cmap='RdYlGn', annot_kws={"size": 15})
    ax.tick_params(labelsize=20)
    plt.show()
    
    
def linear_regression_train_test():
    #Linear regression with L2 regularization
    for i in range(-2, 3):
        alpha = 10**i
        rm = Ridge(alpha = alpha)
        ridge_model = rm.fit(X_train, y_train)
        preds_ridge = ridge_model.predict(X_test)
    
        plt.scatter(preds_ridge, y_test, alpha= 0.75, c= 'b')
        plt.xlabel('Predicted price')
        plt.ylabel('Actual price')
        plt.title('Ridge redularization with alpha {}'.format(alpha))
        overlay = 'R square: {} \nRMSE: {}'.format(ridge_model.score(X_test, y_test), mean_squared_error(y_test, preds_ridge))
        plt.annotate(s = overlay, xy = (12.1, 10.6), size = 'x-large')
        plt.show()
        
def actual_predict_visualization(actual_values, predict_values):
    plt.scatter(actual_values, predict_values, alpha= 0.75, color = 'b')

    plt.xlabel('Predicted price')
    plt.ylabel('Actual price')
    plt.title('Regression Model')
    plt.show()
    
def visualize_original_predict_test(X_val, Y_val, default = "Test"):
    print("Dataset type  : \n" ,default)
    plt.scatter(diabetes_X_test, diabetes_y_test,  color='black')
    plt.plot(diabetes_X_test, diabetes_y_pred, color='blue', linewidth=3)

    plt.xticks(())
    plt.yticks(())
    
    plt.xlabel("X axis", color = "red")
    plt.ylabel("Y axis", color = "green")

    plt.show()
    
    
def visualize_categorical_values(dataset):
    no_of_columns = 4
    no_of_rows = 4
    
    columns_object_type = [i for i in dataset.columns  if dataset[i].dtype == "object"]
    total_rows = (len(columns_object_type) // no_of_rows ) + 1
    
    f, axes = plt.subplots(total_rows, no_of_columns, figsize=(18,24))

    for ind, val in enumerate(columns_object_type):
        sns.countplot(df[val] , ax = axes[ind // no_of_rows , ind %no_of_columns ])
    plt.show()   
    
# sns.pairplot(data = dataset[['arpu_6','arpu_7','arpu_8','churn_flag']],hue = 'churn_flag')

def visualize_pairplot_target(dataset, numberical_col_list , target_val):
    plt.figure(figsize=(18,34))
    sns.pairplot(data = dataset[numberical_col_list],hue = target_val)
    
    #     sns.pairplot(data = dataset[['arpu_6','arpu_7','arpu_8','churn_flag']],hue = 'churn_flag') 
    #check for classification
    plt.show()
    
    
def visualize_numberical_values(dataset):
    plt.figure(figsize=(18,34))
    sns.pairplot(df)
    plt.show()
# visualize_numberical_values(df)
    
def check_skewness_numerical(dataset, target):
    #analysing the distribution of sale price
    print('skew is', dataset.SalePrice.skew())   
    plt.hist(dataset[target], color= 'b')

    plt.title('Distribution of ' + target, fontsize = 24)
    plt.ylabel('observation', fontsize = 20)
    plt.xlabel(target, fontsize = 20)

    plt.show()
    
def skewness_after_log_transform(dataset , target):
    #log transforming sale price to transform it into gaussian distribution
    target1 = np.log(dataset.target)
    print('skew is', target1.skew())
    plt.hist(target, color= 'b')

    plt.title('Distribution of ' + target, fontsize = 24)
    plt.ylabel('observation', fontsize = 20)
    plt.xlabel(target , fontsize = 20)

    plt.show()
    
# Since pairplots for all numeric values together are not clear we can make groups ,do plot with price & analyse

def pair_plot(list_4_numberical_values):
    sns.pairplot(df2, x_vars= list_4_numberical_values, y_vars='SalePrice',size=4, kind='scatter')
    plt.show()

In [118]:
df.shape

(131662, 14)

In [119]:
# corr_2_more_visualize(df)

In [120]:
# visualize_categorical_values(df)

In [121]:


# visualize_numberical_values(df)

In [122]:
#Label encoding
def convert_to_numerical_label_encoding(dataset):
    enc = LabelEncoder()
    for i in dataset.columns:
        if(dataset[i].dtype == "object"):
            dataset[i] = enc.fit_transform(dataset[i])
            
    return dataset

In [123]:
class DataFrameImputer(TransformerMixin):

    def __init__(self):
        """Impute missing values.

        Columns of dtype object are imputed with the most frequent value 
        in column.

        Columns of other types are imputed with mean of column.

        """
    def fit(self, X, y=None):

        self.fill = pd.Series([X[c].value_counts().index[0] if X[c].dtype == np.dtype('O') else X[c].mean() for c in X],
            index=X.columns)

        return self

    def transform(self, X, y=None):
        return X.fillna(self.fill)
    


In [124]:
def majority_imbalanced_dataset(dataset, target_col):
    feature_columns = dataset.columns.tolist()
    feature_columns = [c for c in feature_columns if c not in [target_col]]

    X2_new = dataset[feature_columns]
    Y2_new = dataset[target_col]

    os =  RandomOverSampler(random_state=35)
    X_feature_variables , y_output = os.fit_sample(X2_new, Y2_new)
    
    X_feature_variables[target_col] = y_output
    
    X_feature_variables = X_feature_variables.sample(frac = 1).reset_index(drop = True)
    
    return X_feature_variables

In [125]:
def standardscaler_preprocessing(dataset_train, dataset_test, num_col):
    scaler = StandardScaler()
   
    dataset_train[num_col] = scaler.fit_transform(dataset_train[num_col])

    dataset_test[num_col] = scaler.transform(dataset_test[num_col])
    
    return dataset_train, dataset_test

# <font color ='green' > EDA

In [169]:
 drop_col = ["Var1"]

drop_col = ["Var1"  ]

In [170]:
df1 = df.drop(columns = drop_col)
#df1 = df 
df.shape , df1.shape

((131662, 14), (131662, 13))

In [171]:
df1_test = df_test.drop(columns = drop_col)
#df1_test = df_test
df_test.shape , df1_test.shape

((87395, 13), (87395, 12))

In [129]:
check_cloumn_details_type_categorical(df1)

Columns name :   Trip_ID
{'T0005689460': 1, 'T0005689461': 1, 'T0005689464': 1, 'T0005689465': 1, 'T0005689467': 1, 'T0005689469': 1, 'T0005689470': 1, 'T0005689472': 1, 'T0005689473': 1, 'T0005689474': 1, 'T0005689475': 1, 'T0005689477': 1, 'T0005689479': 1, 'T0005689482': 1, 'T0005689484': 1, 'T0005689485': 1, 'T0005689486': 1, 'T0005689487': 1, 'T0005689491': 1, 'T0005689492': 1, 'T0005689493': 1, 'T0005689496': 1, 'T0005689497': 1, 'T0005689498': 1, 'T0005689501': 1, 'T0005689502': 1, 'T0005689503': 1, 'T0005689504': 1, 'T0005689505': 1, 'T0005689506': 1, 'T0005689507': 1, 'T0005689508': 1, 'T0005689509': 1, 'T0005689510': 1, 'T0005689513': 1, 'T0005689515': 1, 'T0005689516': 1, 'T0005689517': 1, 'T0005689519': 1, 'T0005689520': 1, 'T0005689521': 1, 'T0005689522': 1, 'T0005689523': 1, 'T0005689525': 1, 'T0005689529': 1, 'T0005689530': 1, 'T0005689532': 1, 'T0005689533': 1, 'T0005689534': 1, 'T0005689536': 1, 'T0005689537': 1, 'T0005689538': 1, 'T0005689539': 1, 'T0005689542': 1, 'T

In [172]:
 df1["Type_of_Cab"] = df1["Type_of_Cab"].fillna("Unkown")


In [173]:
 df1["Confidence_Life_Style_Index"] = df1["Confidence_Life_Style_Index"].fillna("Unkown")

In [162]:
#df1 = df1.drop(["Life_Style_Index"], axis = 'columns')

#df1_test = df1_test.drop(["Life_Style_Index"], axis = 'columns')

In [174]:
df2 = DataFrameImputer().fit_transform(df1.copy())


df2_test = DataFrameImputer().fit_transform(df1_test.copy())

In [175]:
df2.isna().sum().sum(), df2_test.isna().sum().sum()

(0, 0)

In [176]:
round(100*(df1.isnull().sum()/len(df1.index)),2) [round(100*(df1.isnull().sum()/len(df1.index)),2).values > 0.00 ].sort_values(ascending = False)

Life_Style_Index         15.34
Customer_Since_Months     4.50
dtype: float64

In [178]:
check_cloumn_details_type_categorical(df1)

Columns name :   Trip_ID
{'T0005689460': 1, 'T0005689461': 1, 'T0005689464': 1, 'T0005689465': 1, 'T0005689467': 1, 'T0005689469': 1, 'T0005689470': 1, 'T0005689472': 1, 'T0005689473': 1, 'T0005689474': 1, 'T0005689475': 1, 'T0005689477': 1, 'T0005689479': 1, 'T0005689482': 1, 'T0005689484': 1, 'T0005689485': 1, 'T0005689486': 1, 'T0005689487': 1, 'T0005689491': 1, 'T0005689492': 1, 'T0005689493': 1, 'T0005689496': 1, 'T0005689497': 1, 'T0005689498': 1, 'T0005689501': 1, 'T0005689502': 1, 'T0005689503': 1, 'T0005689504': 1, 'T0005689505': 1, 'T0005689506': 1, 'T0005689507': 1, 'T0005689508': 1, 'T0005689509': 1, 'T0005689510': 1, 'T0005689513': 1, 'T0005689515': 1, 'T0005689516': 1, 'T0005689517': 1, 'T0005689519': 1, 'T0005689520': 1, 'T0005689521': 1, 'T0005689522': 1, 'T0005689523': 1, 'T0005689525': 1, 'T0005689529': 1, 'T0005689530': 1, 'T0005689532': 1, 'T0005689533': 1, 'T0005689534': 1, 'T0005689536': 1, 'T0005689537': 1, 'T0005689538': 1, 'T0005689539': 1, 'T0005689542': 1, 'T

In [179]:
df3 = convert_to_numerical_label_encoding(df2.copy())
df2.shape, df3.shape

((131662, 13), (131662, 13))

In [180]:
df3_test = convert_to_numerical_label_encoding(df2_test.copy())
df2_test.shape, df3_test.shape

((87395, 12), (87395, 12))

In [182]:
Counter(df3.Life_Style_Index )

Counter({2.42769: 1,
         2.78245: 2,
         2.8020639999461827: 20193,
         3.0345299999999997: 2,
         2.8395799999999998: 4,
         2.81871: 5,
         3.04467: 1,
         2.95887: 3,
         2.9532700000000003: 5,
         2.8487: 2,
         2.6917: 6,
         2.80658: 4,
         2.16167: 1,
         2.6615: 5,
         2.97795: 1,
         2.35974: 1,
         2.82307: 1,
         3.06236: 1,
         2.57278: 1,
         2.48367: 1,
         2.61439: 1,
         2.77751: 6,
         2.70013: 2,
         2.9851: 2,
         2.70044: 2,
         2.70352: 2,
         2.66894: 3,
         2.62154: 3,
         2.5962099999999997: 3,
         2.97894: 3,
         2.6560900000000003: 4,
         2.70134: 4,
         2.47188: 3,
         2.70811: 2,
         2.7719: 2,
         3.21957: 2,
         2.60963: 2,
         2.84043: 1,
         2.99798: 6,
         2.56887: 1,
         2.42948: 3,
         2.89871: 4,
         2.64466: 2,
         2.6858299999999997: 2,


In [183]:

df3 = majority_imbalanced_dataset(df3.copy(), "Surge_Pricing_Type")
 #Counter(df4.Surge_Pricing_Type)

In [184]:
df3.shape

(170184, 13)

In [185]:
df3.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 170184 entries, 0 to 170183
Data columns (total 13 columns):
Trip_ID                        170184 non-null int32
Trip_Distance                  170184 non-null float64
Type_of_Cab                    170184 non-null int32
Customer_Since_Months          170184 non-null float64
Life_Style_Index               170184 non-null float64
Confidence_Life_Style_Index    170184 non-null int32
Destination_Type               170184 non-null int32
Customer_Rating                170184 non-null float64
Cancellation_Last_1Month       170184 non-null int64
Var2                           170184 non-null int64
Var3                           170184 non-null int64
Gender                         170184 non-null int32
Surge_Pricing_Type             170184 non-null int64
dtypes: float64(4), int32(5), int64(4)
memory usage: 13.6 MB


In [187]:
 scaling_col = ["Trip_ID","Trip_Distance" , "Customer_Since_Months" , "Confidence_Life_Style_Index", "Customer_Rating", "Var2", "Var3"]
 #scaling_col = ["Trip_Distance" , "Customer_Since_Months", "Customer_Rating", "Var2", "Var3"]

#scaling_col = ["Trip_Distance" , "Customer_Since_Months" , "Life_Style_Index", "Customer_Rating"]



 df4,df4_test = standardscaler_preprocessing(df3.copy(), df3_test.copy(), scaling_col)

In [188]:
df3.head()

Trip_ID  Trip_Distance  Type_of_Cab  Customer_Since_Months  \
0    46972          29.00            5              10.000000   
1   116778          21.17            2              10.000000   
2    37475          59.43            1               7.000000   
3    68388          39.08            3               4.000000   
4   105540          11.26            1               6.016661   

   Life_Style_Index  Confidence_Life_Style_Index  Destination_Type  \
0          2.802064                            3                 0   
1          3.071570                            2                 0   
2          2.794130                            1                 0   
3          2.802064                            3                 0   
4          2.497030                            1                 0   

   Customer_Rating  Cancellation_Last_1Month  Var2  Var3  Gender  \
0          4.29500                         0    51    65       0   
1          3.67750                         0    49    94       1   
2          1.36500                         2    51    81       1   
3          0.80375                         4    51    81       1   
4          1.40000                         0    47    72       1   

   Surge_Pricing_Type  
0                   2  
1                   2  
2                   2  
3                   3  
4                   2

In [189]:
df3.describe()

Trip_ID  Trip_Distance    Type_of_Cab  Customer_Since_Months  \
count  170184.000000  170184.000000  170184.000000          170184.000000   
mean    65853.421121      43.930058       2.097442               6.005397   
std     38037.306897      25.222330       1.725280               3.550752   
min         0.000000       0.310000       0.000000               0.000000   
25%     32876.750000      24.480000       1.000000               3.000000   
50%     65914.500000      38.100000       2.000000               6.016661   
75%     98842.250000      60.610000       3.000000              10.000000   
max    131661.000000     109.230000       5.000000              10.000000   

       Life_Style_Index  Confidence_Life_Style_Index  Destination_Type  \
count     170184.000000                170184.000000     170184.000000   
mean           2.808098                     1.298089          1.014302   
std            0.208220                     1.038309          1.910293   
min            1.596380                     0.000000          0.000000   
25%            2.693740                     0.000000          0.000000   
50%            2.802064                     1.000000          0.000000   
75%            2.924430                     2.000000          1.000000   
max            4.875110                     3.000000         13.000000   

       Customer_Rating  Cancellation_Last_1Month           Var2  \
count    170184.000000             170184.000000  170184.000000   
mean          2.887436                  0.748308      51.215825   
std           0.976477                  1.016840       4.980607   
min           0.001250                  0.000000      40.000000   
25%           2.195000                  0.000000      48.000000   
50%           2.935000                  0.000000      50.000000   
75%           3.620000                  1.000000      54.000000   
max           5.000000                  8.000000     124.000000   

                Var3         Gender  Surge_Pricing_Type  
count  170184.000000  170184.000000       170184.000000  
mean       75.257045       0.714574            2.000000  
std        11.551148       0.451619            0.816499  
min        52.000000       0.000000            1.000000  
25%        67.000000       0.000000            1.000000  
50%        74.000000       1.000000            2.000000  
75%        82.000000       1.000000            3.000000  
max       206.000000       1.000000            3.000000

In [190]:
X = df3.iloc[:,:-1]

Y = df3.iloc[:,-1]

In [191]:
# Using RFE for finding number of optimal features and applying to the train datasets 

from sklearn.feature_selection import RFE
from sklearn.metrics import r2_score




In [192]:
# model_final = XGBClassifier(
#  learning_rate =0.1,
#  n_estimators=1000,
#  max_depth=5,
#  min_child_weight=1,
#  gamma=0,
#  subsample=0.8,
#  colsample_bytree=0.8,
#  objective= 'multi:softmax',
#  nthread=4,
#  scale_pos_weight=1,
#  num_classes=3,
#  seed=27)

model_final = XGBClassifier(max_depth=5, objective='multi:softmax', num_classes=3)


model_final.fit(X, Y)

y_pred_final = model_final.predict(df3_test)

In [199]:
rfe = RFE(model_final,14)
rfe.fit(X,Y)

RFE(estimator=XGBClassifier(base_score=0.5, booster=None, colsample_bylevel=1,
                            colsample_bynode=1, colsample_bytree=1, gamma=0,
                            gpu_id=-1, importance_type='gain',
                            interaction_constraints=None,
                            learning_rate=0.300000012, max_delta_step=0,
                            max_depth=5, min_child_weight=1, missing=nan,
                            monotone_constraints=None, n_estimators=100,
                            n_jobs=0, num_classes=3, num_parallel_tree=1,
                            objective='multi:softprob', random_state=0,
                            reg_alpha=0, reg_lambda=1, scale_pos_weight=None,
                            subsample=1, tree_method=None,
                            validate_parameters=False, verbosity=None),
    n_features_to_select=14, step=1, verbose=0)

In [202]:
rfe_scores = pd.DataFrame(list(zip(X.columns,rfe.support_,rfe.ranking_)))
rfe_scores.columns = ['Column_Names','Status','Rank']

In [203]:
rfe_scores.head()

Column_Names  Status  Rank
0                Trip_ID    True     1
1          Trip_Distance    True     1
2            Type_of_Cab    True     1
3  Customer_Since_Months    True     1
4       Life_Style_Index    True     1

In [196]:
submission_1 = submission.copy()

print(df_test.shape , submission.shape , len(y_pred_final))

submission_1["Surge_Pricing_Type"] = y_pred_final

print(submission_1["Surge_Pricing_Type"].values)


submission_1.to_csv('XGBoost_drop_gender.csv', index=False)

df_submission_1 = pd.read_csv('XGBoost_drop_gender.csv')

print(df_submission_1.shape)

df_submission_1.head(3)

(87395, 13) (87395, 2) 87395
[2 2 2 ... 1 3 2]
(87395, 2)


Trip_ID  Surge_Pricing_Type
0  T0005689459                   2
1  T0005689462                   2
2  T0005689463                   2

In [65]:
print( df["Trip_Distance"].max() , df["Trip_Distance"].min() , df["Trip_Distance"].mean())

print( df["Customer_Since_Months"].max() , df["Customer_Since_Months"].min() , df["Customer_Since_Months"].mean())

print( df["Life_Style_Index"].max() , df["Life_Style_Index"].min() , df["Life_Style_Index"].mean())

print( df["Customer_Rating"].max() , df["Customer_Rating"].min() , df["Customer_Rating"].mean())


109.23 0.31 44.20090853853045
10.0 0.0 6.016661099712109
4.87511 1.59638 2.8020639999461827
5.0 0.00125 2.849457958636489


In [161]:
def get_accuracy(y_train_val , y_pred_val , dataset_type = "Default"):
    
    print(" Dataset type is : ", dataset_type)
    
    print("\n Accuracy Score     : ",round(accuracy_score(y_train_val, y_pred_val), 4) * 100)
    
    print("\n precision_accuracy : ",round(precision_score(y_train_val, y_pred_val), 4) * 100)
 
    print("\n recall_accuracy    : ",round(recall_score(y_train_val, y_pred_val), 4) * 100)
    
    print("\n roc_auc_accuracy   : ",round(roc_auc_score(y_train_val, y_pred_val), 4) * 100)
    
    print("\n f1_score_accuracy  : ",round(f1_score(y_train_val, y_pred_val), 4) * 100)
    
    print("\n explained_variance  : ",round(explained_variance_score(y_train_val, y_pred_val), 4) * 100)
    
    tn, fp, fn, tp = confusion_matrix(y_train_val, y_pred_val).ravel()
    
    print("\n Confusion Matrix TN : ", tn, " FP : ", fp, " FN : ", fn, " TP : ", tp)

In [162]:

rows=[]

def addRandomStateForAlgorithm(x,y,names,algorithms,columns_name,random_state_list):    
    for j in range(len(algorithms)):
        model = algorithms[j]
        for i in random_state_list:
            
            x_train, x_test , y_train , y_test = train_test_split(x ,y , test_size = 0.30 , random_state = i)
            
            model.fit(x_train,y_train)
            
            y_pred_train = model.predict(x_train)
            y_pred = model.predict(x_test)
            
            train_acc = accuracy_score(y_train, y_pred_train)
            train_acc = round(train_acc, 4) * 100
            
            test_acc = accuracy_score(y_test, y_pred)
            test_acc = round(test_acc, 4) * 100
            
#             roc_auc_score_acc = roc_auc_score(y_test, y_pred)
#             roc_auc_score_acc = round(roc_auc_score_acc, 4) * 100
            

#             row = [names[j],   i,   train_acc, test_acc, roc_auc_score_acc]
            row = [names[j],   i,   train_acc, test_acc]
    
            rows.append(row)
            
    models_df = pd.DataFrame(rows) 
    
    models_df.columns = columns_name
    print(models_df)
    

In [163]:
   
# names_regression = [ "LightGBM", "RF", "XGBoost" , "SVM"]
# algorithms = [ LGBMClassifier(), RandomForestClassifier(), XGBClassifier(), SVC()]

# columns_name = ["Model",    "Random_state",   'Train_acc',     "Test_acc" , "roc_auc_score"]

names_regression = [ "XGBClassifier"]
algorithms = [ XGBClassifier(max_depth=5, objective='multi:softmax', num_classes=3)]

columns_name = ["Model",    "Random_state",   'Train_acc',     "Test_acc" ]


random_state_list_up_to_10 = [1]


addRandomStateForAlgorithm(X,Y,names_regression,algorithms,columns_name,random_state_list_up_to_10)

           Model  Random_state  Train_acc  Test_acc
0  XGBClassifier             1      70.68     70.01


(87395, 13) (87395, 2) 87395
[1 2 2 ... 1 2 2]
(87395, 2)


Trip_ID  Surge_Pricing_Type
0  T0005689459                   1
1  T0005689462                   2
2  T0005689463                   2

In [100]:
#train : train is a dataset

In [101]:
#Dataset : train & test


In [103]:
df.columns

Index(['Trip_ID', 'Trip_Distance', 'Type_of_Cab', 'Customer_Since_Months',
       'Life_Style_Index', 'Confidence_Life_Style_Index', 'Destination_Type',
       'Customer_Rating', 'Cancellation_Last_1Month', 'Var1', 'Var2', 'Var3',
       'Gender', 'Surge_Pricing_Type'],
      dtype='object')

In [104]:
Counter(df.Surge_Pricing_Type)

Counter({2: 56728, 3: 47720, 1: 27214})

In [109]:
df3[0:87395].shape  , df3[87395 : ].shape

((87395, 12), (44267, 12))

In [141]:
def majority_imbalanced_dataset(dataset, target_col):
    feature_columns = dataset.columns.tolist()
    feature_columns = [c for c in feature_columns if c not in [target_col]]

    X2 = dataset[feature_columns]
    Y2 = dataset[target_col]

    os =  RandomOverSampler(random_state=35)
    X_feature_variables , y_output = os.fit_sample(X2, Y2)
    
    return X_feature_variables , y_output

In [142]:
X_feature_variables1 , y_output1 = majority_imbalanced_dataset(df3, "Surge_Pricing_Type")

In [143]:
df10 = X_feature_variables1.copy()

In [145]:
df10["Surge_Pricing_Type"] = y_output1

In [146]:
df10.head()

Trip_Distance  Type_of_Cab  Customer_Since_Months  Life_Style_Index  \
0      -1.466568            1              -1.415378     -1.801959e+00   
1      -0.577167            1               1.123841     -9.440728e-02   
2      -0.102689            1               1.123841      3.633778e-14   
3       0.680141            2               1.123841      3.633778e-14   
4       0.421157            2               1.123841      1.118919e+00   

   Confidence_Life_Style_Index  Destination_Type  Customer_Rating  \
0                            0                 0         1.076346   
1                            1                 0         0.612378   
2                            1                 4         0.664638   
3                            1                 0         0.616202   
4                            1                 0         0.563942   

   Cancellation_Last_1Month      Var2      Var3  Gender  Surge_Pricing_Type  
0                         0 -1.043456 -1.304086       0                   2  
1                         0  0.962110  0.250555       1                   2  
2                         2  0.962110  0.164186       1                   2  
3                         0  0.159884 -0.094921       1                   3  
4                         4 -0.441786  2.323410       1                   2

In [148]:
df10.shape , df3.shape

((170184, 12), (131662, 12))

In [162]:
new_test = df10[0:87395]

new_train = df10[87395 : ] 

In [163]:
x1_train = new_train.iloc[:, :-1]
y1_train = new_train.iloc[:, -1]

In [164]:
x1_test = new_test.iloc[:, :-1]
y1_test = new_test.iloc[:, -1]

In [152]:
model_final = XGBClassifier(max_depth=5, objective='multi:softmax', num_classes=3)


model_final.fit(x1_train, y1_train)


y_pred_final_new_train = model_final.predict(x1_train)

# y_pred_final_new_test = model_final.predict(x1_test)

In [166]:
len(y1_test)

87395

In [167]:
y_pred_final_new_test = model_final.predict(df3_test)

In [ ]:
y_

In [154]:
get_accuracy(y1_train , y_pred_final_new_train ,  "Train")

 Dataset type is :  Train

 Accuracy Score     :  69.41000000000001
[[32209  3577  2880]
 [ 7132  7910  3973]
 [ 3632  4130 17346]]


In [156]:
get_accuracy(y1_test , y_pred_final_new_test ,  "Test")

 Dataset type is :  Test

 Accuracy Score     :  32.190000000000005
[[ 6722  4775  6565]
 [14185  9913 13615]
 [11743  8379 11498]]


In [137]:
get_accuracy(y1_test , y_pred_final_new_test ,  "Their Test")

 Dataset type is :  Their Test

 Accuracy Score     :  37.980000000000004
[[ 2570 10011  5481]
 [ 5323 21140 11250]
 [ 4447 17693  9480]]


In [157]:
def get_accuracy(y_train_val , y_pred_val , dataset_type = "Default"):
    
    print(" Dataset type is : ", dataset_type)
    
    print("\n Accuracy Score     : ",round(accuracy_score(y_train_val, y_pred_val), 4) * 100)
    
#     print("\n precision_accuracy : ",round(precision_score(y_train_val, y_pred_val), 4) * 100)
 
#     print("\n recall_accuracy    : ",round(recall_score(y_train_val, y_pred_val), 4) * 100)
    
#     print("\n roc_auc_accuracy   : ",round(roc_auc_score(y_train_val, y_pred_val), 4) * 100)
    
#     print("\n f1_score_accuracy  : ",round(f1_score(y_train_val, y_pred_val), 4) * 100)
    
#     print("\n explained_variance  : ",round(explained_variance_score(y_train_val, y_pred_val), 4) * 100)
    
#     tn, fp, fn, tp = confusion_matrix(y_train_val, y_pred_val).ravel()
    
#     print("\n Confusion Matrix TN : ", tn, " FP : ", fp, " FN : ", fn, " TP : ", tp)
    print(confusion_matrix(y_train_val, y_pred_val))

In [158]:
submission_new["Surge_Pricing_Type"] = y_pred_final_new_test


submission_new.to_csv('submission_new_imbalance.csv', index=False)


In [159]:
submission_new.shape , submission.shape

((87395, 2), (87395, 2))